In [1]:
#!pip install mne scipy
#!pip install pandas numpy openpyxl
#!pip install tsfresh
#!pip install PyWavelets

In [1]:
import os
import numpy as np
import scipy.signal as signal
import mne

def process_all_eeg_data() -> dict:
    """
    Process all .bdf EEG files in the current directory, applying filters and extracting data from
    channels A15 (O1), A16 (Oz), and A17 (O2).

    Returns
    -------
    dict
        A dictionary containing processed EEG data and header information for each file.
    """
    # Get a list of all .bdf files in the current directory
    files = [f for f in os.listdir('.') if f.endswith('.bdf')]
    if not files:
        raise FileNotFoundError("No BDF files found in the current directory")
    
    # Initialize the results dictionary
    results = {}
    
    # Loop over each file
    for filename in files:
        full_file_path = os.path.join(os.getcwd(), filename)
        
        # Read the raw EEG data using MNE
        raw = mne.io.read_raw_bdf(full_file_path, preload=True)
        hdr = raw.info
        
        # Select data from channels A15 (O1), A16 (Oz), and A17 (O2)
        channels_select = ['A15', 'A16', 'A17']
        missing_channels = [ch for ch in channels_select if ch not in hdr['ch_names']]
        if missing_channels:
            raise ValueError(f"Selected channels {missing_channels} not found in the data")
        
        channel_indices = [hdr['ch_names'].index(ch) for ch in channels_select]
        EEG_data = raw.get_data(picks=channel_indices).T  # Shape: (n_samples, n_channels)
        
        # Filter EEG Data
        Fs = hdr['sfreq']  # Sampling frequency
        
        # Bandpass filter parameters (2 to 80 Hz)
        Fc_BP = [2, 80]  # Bandpass frequency range
        Wn_BP = [f / (Fs / 2) for f in Fc_BP]  # Normalize by Nyquist frequency
        
        # Create and apply bandpass filter (6th order zero-phase Butterworth IIR)
        B_BP, A_BP = signal.butter(3, Wn_BP, btype='bandpass')
        EEG_filtered_BP = signal.filtfilt(B_BP, A_BP, EEG_data, axis=0)
        
        # Band stop filter parameters (48 to 52 Hz)
        Fc_BS = [48, 52]  # Band stop frequency range
        Wn_BS = [f / (Fs / 2) for f in Fc_BS]  # Normalize by Nyquist frequency
        
        # Create and apply band stop filter (6th order zero-phase Butterworth IIR)
        B_BS, A_BS = signal.butter(3, Wn_BS, btype='bandstop')
        EEG_filtered = signal.filtfilt(B_BS, A_BS, EEG_filtered_BP, axis=0)
        
        # Extract prefix before underscore from the filename
        underscore_index = filename.find('_')
        if underscore_index == -1:
            raise ValueError(f"Filename format error, no underscore found in {filename}")
        key = filename[:underscore_index]
        
        # Store results in the dictionary
        results[key] = {
            'data': EEG_filtered,      # Filtered data for channels A15, A16, A17
            'channels': channels_select,  # List of channel names
            'header': hdr
        }
        
        # Display a message indicating successful processing
        print(f"Data for file {filename} processed successfully")
    
    return results


In [2]:
results = process_all_eeg_data()

Extracting EDF parameters from c:\Users\WERPELGA\OneDrive - Danone\Desktop\UoA\2024.1&2\Python Gabe\A1_Full_Block.bdf...
BDF file detected
Setting channel info structure...
Creating raw.info structure...
Reading 0 ... 739327  =      0.000 ...   361.000 secs...
Data for file A1_Full_Block.bdf processed successfully
Extracting EDF parameters from c:\Users\WERPELGA\OneDrive - Danone\Desktop\UoA\2024.1&2\Python Gabe\A3_Full_Block.bdf...
BDF file detected
Setting channel info structure...
Creating raw.info structure...
Reading 0 ... 757759  =      0.000 ...   370.000 secs...
Data for file A3_Full_Block.bdf processed successfully
Extracting EDF parameters from c:\Users\WERPELGA\OneDrive - Danone\Desktop\UoA\2024.1&2\Python Gabe\A4_Full_Block.bdf...
BDF file detected
Setting channel info structure...
Creating raw.info structure...
Reading 0 ... 782335  =      0.000 ...   382.000 secs...
Data for file A4_Full_Block.bdf processed successfully
Extracting EDF parameters from c:\Users\WERPELGA\One

In [3]:
import numpy as np
import pandas as pd

def segment_eeg_data_new(results: dict, cohort_file: str = 'Cohort.xlsx') -> dict:
    """
    Segments EEG data into predefined sections (EC, EO, LC, RC, DEC, NDEC) based on cohort information,
    removing the first 2 seconds from each section.

    Parameters
    ----------
    results : dict
        Dictionary containing the raw EEG data and header information for each key (participant).
    cohort_file : str, optional
        Path to the Excel file containing cohort information (default is 'Cohort.xlsx').

    Returns
    -------
    dict
        Dictionary containing segmented EEG data for each participant.
    """
    # Read the cohort information from an Excel file
    cohort_table = pd.read_excel(cohort_file)
    # Segment Duration (in seconds)
    segment_duration = 10  # Original segment duration in seconds
    skip_duration = 2      # Duration to skip at the start of each segment (2 seconds)

    # Initialize the segmented results dictionary
    segmented_data = {}

    # Iterate through each key in the results dictionary
    for key, result in results.items():
        data = result['data']  # Data shape: (n_samples, n_channels)
        hdr = result['header']

        # Find the matching row in the cohort table
        cohort_row = cohort_table[cohort_table['Cohort'] == key]
        
        if cohort_row.empty:
            raise ValueError(f"Cohort information not found for {key}")

        # Define the sample rate and calculate sample counts
        Fs = hdr['sfreq']  # Sampling frequency
        samples_per_segment = int(segment_duration * Fs)
        samples_to_skip = int(skip_duration * Fs)
        effective_samples_per_segment = samples_per_segment - samples_to_skip
        n_channels = data.shape[1]  # Number of channels (should be 3: O1, Oz, O2)

        # Initialize segments with zeros
        EC = np.zeros((effective_samples_per_segment, n_channels))
        EO = np.zeros((effective_samples_per_segment, n_channels))
        LC = np.zeros((effective_samples_per_segment, n_channels))
        RC = np.zeros((effective_samples_per_segment, n_channels))
        DEC = np.zeros((effective_samples_per_segment, n_channels))
        NDEC = np.zeros((effective_samples_per_segment, n_channels))

        # Fill segments with data if available, skipping the first 2 seconds
        # EC segment
        segment_start = 0
        segment_end = samples_per_segment
        if data.shape[0] >= segment_end:
            EC = data[segment_start + samples_to_skip : segment_end, :]
        else:
            print(f"Not enough data for EC segment in {key}")

        # EO segment
        segment_start = samples_per_segment
        segment_end = 2 * samples_per_segment
        if data.shape[0] >= segment_end:
            EO = data[segment_start + samples_to_skip : segment_end, :]
        else:
            print(f"Not enough data for EO segment in {key}")

        # LC segment
        segment_start = 2 * samples_per_segment
        segment_end = 3 * samples_per_segment
        if data.shape[0] >= segment_end:
            LC = data[segment_start + samples_to_skip : segment_end, :]
        else:
            print(f"Not enough data for LC segment in {key}")

        # RC segment
        segment_start = 3 * samples_per_segment
        segment_end = 4 * samples_per_segment
        if data.shape[0] >= segment_end:
            RC = data[segment_start + samples_to_skip : segment_end, :]
        else:
            print(f"Not enough data for RC segment in {key}")

        # Apply conditions based on cohort table
        if cohort_row['LC'].values[0] == 'DEC':
            # Assign 'DEC' to LC and 'NDEC' to RC
            DEC = LC
            NDEC = RC
        elif cohort_row['RC'].values[0] == 'DEC':
            # Assign 'DEC' to RC and 'NDEC' to LC
            DEC = RC
            NDEC = LC
        else:
            # If neither LC nor RC is 'DEC', assign NDEC accordingly
            NDEC = LC
            # Optionally handle cases where DEC is not specified
            DEC = RC  # Or set DEC to zeros if appropriate

        # Store the segmented data and 'LinesDifference' in the results dictionary
        segmented_data[key] = {
            'header': hdr,
            'EC': EC,
            'EO': EO,
            'DEC': DEC,
            'NDEC': NDEC,
            'LinesDifference': cohort_row['LinesDifference'].values[0]
        }

    return segmented_data


In [4]:
segmented_data = segment_eeg_data_new(results)

In [5]:
import pandas as pd
import numpy as np
from tsfresh import extract_features, select_features
from tsfresh.utilities.dataframe_functions import impute
from sklearn.model_selection import train_test_split
from sklearn.ensemble import RandomForestClassifier
from sklearn.metrics import classification_report

def prepare_time_series_by_section(segmented_data, cohort_table):
    """
    Prepares a DataFrame suitable for tsfresh from segmented EEG data for all sections (EC, EO, DEC, NDEC).

    Parameters
    ----------
    segmented_data : dict
        The dictionary containing segmented EEG data for each participant.
    cohort_table : pd.DataFrame
        DataFrame containing cohort information (including labels for Amblyopia/Control).

    Returns
    -------
    pd.DataFrame, pd.Series
        A DataFrame where each row represents a time-series sample with columns 'id', 'time', 'O1', 'Oz', 'O2',
        and a Series with group labels indexed by 'id'.
    """
    data_list = []
    labels_list = []

    # Loop through each participant's data
    for key, value in segmented_data.items():
        # Find the matching cohort row
        cohort_row = cohort_table[cohort_table['Cohort'] == key]
        if cohort_row.empty:
            continue

        # Assign label based on the first letter of the 'Cohort' column (Amblyopia = 1, Control = 0)
        label = 1 if key.startswith('A') else 0

        # Get channel names; default to ['O1', 'Oz', 'O2'] if not available
        channels = value.get('channels', ['O1', 'Oz', 'O2'])

        # For each section (EC, EO, DEC, NDEC)
        for section in ['EC', 'EO', 'DEC', 'NDEC']:
            section_data = value[section]  # Shape: (n_samples, n_channels)

            # Create a DataFrame for this section
            n_samples = section_data.shape[0]
            df = pd.DataFrame({
                'id': f"{key}_{section}",
                'time': np.arange(n_samples)
            })

            # Add each channel's data as a column
            for idx, channel_name in enumerate(channels):
                df[channel_name] = section_data[:, idx]

            # Append to data list
            data_list.append(df)

            # Append label for this 'id' (participant_section)
            labels_list.append({'id': f"{key}_{section}", 'label': label})

    # Concatenate all data into a single DataFrame
    time_series_df = pd.concat(data_list, ignore_index=True)

    # Create a labels DataFrame and convert to a Series indexed by 'id'
    labels_df = pd.DataFrame(labels_list).drop_duplicates(subset='id')
    labels_series = labels_df.set_index('id')['label']

    # Return the time-series data and corresponding labels
    return time_series_df, labels_series

# Load your cohort table (must include 'Cohort' column)
cohort_table = pd.read_excel('Cohort.xlsx')

# Prepare the time series DataFrame and labels
time_series_df, labels = prepare_time_series_by_section(segmented_data, cohort_table)


In [9]:
# Import necessary libraries
from sklearn.ensemble import RandomForestClassifier, GradientBoostingClassifier
from sklearn.neural_network import MLPClassifier
from xgboost import XGBClassifier
from sklearn.linear_model import LogisticRegression
from sklearn.svm import SVC
from sklearn.feature_selection import SelectKBest, f_classif
from sklearn.model_selection import train_test_split
from sklearn.metrics import (
    classification_report, confusion_matrix, accuracy_score, precision_score,
    recall_score, f1_score, matthews_corrcoef
)
from sklearn.preprocessing import StandardScaler
from sklearn.pipeline import Pipeline
from tsfresh import extract_features
from tsfresh.feature_extraction import EfficientFCParameters, MinimalFCParameters
from tsfresh.utilities.dataframe_functions import impute
import pandas as pd
import numpy as np
import gc
import pickle
import os
import scipy.stats as stats

# Assume that 'time_series_df' is already defined

# 0. Preprocessing: Remove specific amblyope IDs
# Find all unique IDs starting with 'A1'
amblyope_ids = time_series_df['id'].unique()
amblyope_ids = [id_ for id_ in amblyope_ids if id_.startswith('A1')]

# Remove selected amblyope IDs
amblyope_ids_to_remove = amblyope_ids[:4]  # First four IDs
df_modified = time_series_df[~time_series_df['id'].isin(amblyope_ids_to_remove)].copy()

# Extract unique IDs from the modified DataFrame
unique_ids = df_modified['id'].unique()

# Select only the required columns
df_modified = df_modified[['id', 'time', 'O1', 'Oz', 'O2']]

# Reset indexes
df_modified.reset_index(drop=True, inplace=True)

# 1. Create a custom fc_parameters dictionary
efficient_fc_parameters = EfficientFCParameters()

# Create custom fc_parameters with the specified feature calculators
custom_fc_parameters = {
    'fft_coefficient': [
        {'coeff': coeff, 'attr': attr}
        for coeff in range(100)  # Adjust the range as needed
        for attr in ['real', 'imag', 'abs', 'angle']
    ],
    'ar_coefficient': [
        {'k': 10, 'coeff': coeff} for coeff in range(1, 11)
    ],
    'augmented_dickey_fuller': [
        {'attr': 'teststat'},
        {'attr': 'pvalue'},
        {'attr': 'usedlag'}
    ],
    'large_standard_deviation': [
        {'r': 0.2}
    ],
    'number_peaks': [
        {'n': n} for n in [1, 5]
    ],
    'fourier_entropy': [
        {'bins': 10}
    ],
    'ratio_beyond_r_sigma': [
        {'r': 1}
    ]
}

# Append MinimalFCParameters to custom_fc_parameters
minimal_fc_parameters = MinimalFCParameters()
custom_fc_parameters.update(minimal_fc_parameters)

# 2. Extract features only once
def process_in_chunks(df_modified, N, fc_parameters):
    # Get unique IDs
    unique_ids = df_modified['id'].unique()
    
    # Split the unique IDs into chunks of size N
    chunks = [unique_ids[i:i + N] for i in range(0, len(unique_ids), N)]
    
    # Initialize an empty list to store the results
    results = []
    
    # Process each chunk
    for chunk in chunks:
        # Filter the DataFrame to include only the IDs in the current chunk
        chunk_df = df_modified[df_modified['id'].isin(chunk)]
        
        # Extract features for the current chunk using the custom fc_parameters
        extracted_features_chunk = extract_features(
            chunk_df,
            column_id='id',
            column_sort='time',
            default_fc_parameters=fc_parameters,
            n_jobs=4,
        )
        
        # Impute missing values in the extracted features
        impute(extracted_features_chunk)
        
        # Append the extracted features to the results list
        results.append(extracted_features_chunk)
        
        # Clear memory
        del chunk_df, extracted_features_chunk
        gc.collect()
    
    # Concatenate all the results into a single DataFrame
    final_result = pd.concat(results)
    
    return final_result

# Set the chunk size N (adjust based on your memory constraints)
N = 1  # Adjust based on your memory constraints

# Extract features only once
extracted_features = process_in_chunks(df_modified, N, custom_fc_parameters)

# Clean the extracted features
extracted_features_clean = extracted_features.replace([np.inf, -np.inf], np.nan).dropna(axis=1)

# Ensure that the labels are aligned with the extracted features
def get_label_from_id(id_):
    if id_.startswith('A'):
        return 1  # Amblyope
    elif id_.startswith('C'):
        return 0  # Control
    else:
        return np.nan

labels = pd.DataFrame(extracted_features_clean.index, columns=['id'])
labels['label'] = labels['id'].apply(get_label_from_id)
labels.set_index('id', inplace=True)
labels_aligned = labels.loc[extracted_features_clean.index]

# 3. Define classifiers (using default parameters for simplicity)
classifiers = {
    'Random Forest': RandomForestClassifier(random_state=42),
    'Gradient Boosting': GradientBoostingClassifier(random_state=42),
    'Neural Network': MLPClassifier(random_state=42, max_iter=1000),
    'Logistic Regression': LogisticRegression(random_state=42, max_iter=5000),
    'Support Vector Machine': SVC(random_state=42),
    'XGBoost': XGBClassifier(random_state=42, use_label_encoder=False, eval_metric='logloss')
}

# 4. Define the number of permutations
num_permutations = 4  # Adjust as needed

# Initialize metrics dictionary
metrics = {name: {'accuracy': [], 'precision': [], 'recall': [], 'f1_score': [], 'mcc': []} for name in classifiers.keys()}

# 5. Loop over permutations
for perm in range(num_permutations):
    print(f"\nPermutation {perm+1}/{num_permutations}")
    
    # Shuffle the labels
    np.random.seed(perm)  # For reproducibility
    shuffled_labels = labels_aligned['label'].sample(frac=1, random_state=perm).reset_index(drop=True)
    
    # Split the data into training and testing sets
    X_train, X_test, y_train, y_test = train_test_split(
        extracted_features_clean,
        shuffled_labels,
        test_size=0.25,
        random_state=42,
        stratify=shuffled_labels
    )
    
    # Loop through each classifier and evaluate
    for name, classifier in classifiers.items():
        print(f"Evaluating {name} for permutation {perm+1}...")
        # Create a pipeline with feature selection and the classifier
        if name in ['Neural Network', 'Logistic Regression', 'Support Vector Machine']:
            pipeline = Pipeline([
                ('scaler', StandardScaler()),
                ('selector', SelectKBest(f_classif, k=50)),
                ('classifier', classifier)
            ])
        else:
            pipeline = Pipeline([
                ('selector', SelectKBest(f_classif, k=50)),
                ('classifier', classifier)
            ])
        
        # Fit the pipeline
        pipeline.fit(X_train, y_train)
        
        # Make predictions
        y_pred = pipeline.predict(X_test)
        
        # Calculate metrics
        accuracy = accuracy_score(y_test, y_pred)
        precision = precision_score(y_test, y_pred, zero_division=0)
        recall = recall_score(y_test, y_pred, zero_division=0)
        f1 = f1_score(y_test, y_pred, zero_division=0)
        mcc = matthews_corrcoef(y_test, y_pred)
        
        # Append metrics
        metrics[name]['accuracy'].append(accuracy)
        metrics[name]['precision'].append(precision)
        metrics[name]['recall'].append(recall)
        metrics[name]['f1_score'].append(f1)
        metrics[name]['mcc'].append(mcc)

# 6. After permutations, compute mean and 95% confidence intervals
def compute_confidence_interval(data):
    n = len(data)
    mean = np.mean(data)
    sem = stats.sem(data)
    h = sem * stats.t.ppf((1 + 0.95) / 2., n-1)
    return mean, mean - h, mean + h

# Print the results
for name in classifiers.keys():
    print(f"\nResults for {name}:")
    for metric_name in ['accuracy', 'precision', 'recall', 'f1_score', 'mcc']:
        data = metrics[name][metric_name]
        mean, lower, upper = compute_confidence_interval(data)
        print(f"{metric_name.capitalize()}: {mean:.4f}, 95% CI: [{lower:.4f}, {upper:.4f}]")




Feature Extraction: 100%|██████████| 3/3 [00:06<00:00,  2.06s/it]



Permutation 1/4
Evaluating Random Forest for permutation 1...


c:\Users\WERPELGA\AppData\Local\Programs\Python\Python39\lib\site-packages\sklearn\feature_selection\_univariate_selection.py:112: UserWarning: Features [   1  413  421  429  841  849  857 1269 1277] are constant.
  warnings.warn("Features %s are constant." % constant_features_idx, UserWarning)
c:\Users\WERPELGA\AppData\Local\Programs\Python\Python39\lib\site-packages\sklearn\feature_selection\_univariate_selection.py:113: RuntimeWarning: invalid value encountered in divide
  f = msb / msw


Evaluating Gradient Boosting for permutation 1...


c:\Users\WERPELGA\AppData\Local\Programs\Python\Python39\lib\site-packages\sklearn\feature_selection\_univariate_selection.py:112: UserWarning: Features [   1  413  421  429  841  849  857 1269 1277] are constant.
  warnings.warn("Features %s are constant." % constant_features_idx, UserWarning)
c:\Users\WERPELGA\AppData\Local\Programs\Python\Python39\lib\site-packages\sklearn\feature_selection\_univariate_selection.py:113: RuntimeWarning: invalid value encountered in divide
  f = msb / msw


...

Evaluating Neural Network for permutation 4...


c:\Users\WERPELGA\AppData\Local\Programs\Python\Python39\lib\site-packages\sklearn\feature_selection\_univariate_selection.py:112: UserWarning: Features [   1  413  421  429  841  849  857 1269 1277] are constant.
  warnings.warn("Features %s are constant." % constant_features_idx, UserWarning)
c:\Users\WERPELGA\AppData\Local\Programs\Python\Python39\lib\site-packages\sklearn\feature_selection\_univariate_selection.py:113: RuntimeWarning: invalid value encountered in divide
  f = msb / msw


Evaluating Logistic Regression for permutation 4...
Evaluating Support Vector Machine for permutation 4...
Evaluating XGBoost for permutation 4...


c:\Users\WERPELGA\AppData\Local\Programs\Python\Python39\lib\site-packages\sklearn\feature_selection\_univariate_selection.py:112: UserWarning: Features [   1  413  421  429  841  849  857 1269 1277] are constant.
  warnings.warn("Features %s are constant." % constant_features_idx, UserWarning)
c:\Users\WERPELGA\AppData\Local\Programs\Python\Python39\lib\site-packages\sklearn\feature_selection\_univariate_selection.py:113: RuntimeWarning: invalid value encountered in divide
  f = msb / msw
c:\Users\WERPELGA\AppData\Local\Programs\Python\Python39\lib\site-packages\sklearn\feature_selection\_univariate_selection.py:112: UserWarning: Features [   1  413  421  429  841  849  857 1269 1277] are constant.
  warnings.warn("Features %s are constant." % constant_features_idx, UserWarning)
c:\Users\WERPELGA\AppData\Local\Programs\Python\Python39\lib\site-packages\sklearn\feature_selection\_univariate_selection.py:113: RuntimeWarning: invalid value encountered in divide
  f = msb / msw
c:\Users\W


Results for Random Forest:
Accuracy: 0.4792, 95% CI: [0.3123, 0.6460]
Precision: 0.4554, 95% CI: [0.2310, 0.6797]
Recall: 0.3750, 95% CI: [-0.0228, 0.7728]
F1_score: 0.3913, 95% CI: [0.0750, 0.7077]
Mcc: -0.0461, 95% CI: [-0.3960, 0.3038]

Results for Gradient Boosting:
Accuracy: 0.5000, 95% CI: [0.3125, 0.6875]
Precision: 0.5179, 95% CI: [0.2940, 0.7417]
Recall: 0.4583, 95% CI: [0.2044, 0.7122]
F1_score: 0.4733, 95% CI: [0.2865, 0.6600]
Mcc: 0.0070, 95% CI: [-0.3789, 0.3930]

Results for Neural Network:
Accuracy: 0.5833, 95% CI: [0.4751, 0.6916]
Precision: 0.6054, 95% CI: [0.4380, 0.7728]
Recall: 0.5417, 95% CI: [0.4091, 0.6743]
F1_score: 0.5652, 95% CI: [0.4812, 0.6493]
Mcc: 0.1729, 95% CI: [-0.0569, 0.4027]

Results for Logistic Regression:
Accuracy: 0.6042, 95% CI: [0.4373, 0.7710]
Precision: 0.6202, 95% CI: [0.4725, 0.7680]
Recall: 0.5417, 95% CI: [0.2080, 0.8754]
F1_score: 0.5648, 95% CI: [0.3382, 0.7914]
Mcc: 0.2171, 95% CI: [-0.1193, 0.5536]

Results for Support Vector Machine

In [24]:
# Import necessary libraries
from sklearn.ensemble import RandomForestClassifier, GradientBoostingClassifier
from sklearn.neural_network import MLPClassifier
from xgboost import XGBClassifier
from sklearn.linear_model import LogisticRegression
from sklearn.svm import SVC
from sklearn.feature_selection import SelectKBest, f_classif
from sklearn.model_selection import train_test_split
from sklearn.metrics import (
    accuracy_score, precision_score, recall_score, f1_score, matthews_corrcoef
)
from sklearn.preprocessing import StandardScaler
from sklearn.pipeline import Pipeline
from tsfresh import extract_features
from tsfresh.feature_extraction import EfficientFCParameters, MinimalFCParameters
from tsfresh.utilities.dataframe_functions import impute
import pandas as pd
import numpy as np
import gc
import os
import scipy.stats as stats
import warnings
from sklearn.exceptions import ConvergenceWarning

# Assume that 'time_series_df' is already defined

# Define the IDs to remove in each run
ids_to_remove_list = ['A1','A3','A4', 'A6', 'A7', 'A8', 'A9']

# 1. Create a custom fc_parameters dictionary (same as before)
# Load EfficientFCParameters
efficient_fc_parameters = EfficientFCParameters()

# Create custom fc_parameters with the specified feature calculators
custom_fc_parameters = {
    'fft_coefficient': [
        {'coeff': coeff, 'attr': attr}
        for coeff in range(100)  # Adjust the range as needed
        for attr in ['real', 'imag', 'abs', 'angle']
    ],
    'ar_coefficient': [
        {'k': 10, 'coeff': coeff} for coeff in range(1, 11)
    ],
    'augmented_dickey_fuller': [
        {'attr': 'teststat'},
        {'attr': 'pvalue'},
        {'attr': 'usedlag'}
    ],
    'large_standard_deviation': [
        {'r': 0.2}
    ],
    'number_peaks': [
        {'n': n} for n in [1, 5]
    ],
    'fourier_entropy': [
        {'bins': 10}
    ],
    'ratio_beyond_r_sigma': [
        {'r': 1}
    ]
}

# Append MinimalFCParameters to custom_fc_parameters
minimal_fc_parameters = MinimalFCParameters()
custom_fc_parameters.update(minimal_fc_parameters)

# 2. Define the function to process data in chunks using the custom fc_parameters
def process_in_chunks(df_modified, N, fc_parameters):
    # Get unique IDs
    unique_ids = df_modified['id'].unique()
    
    # Split the unique IDs into chunks of size N
    chunks = [unique_ids[i:i + N] for i in range(0, len(unique_ids), N)]
    
    # Initialize an empty list to store the results
    results = []
    
    # Process each chunk
    for chunk in chunks:
        # Filter the DataFrame to include only the IDs in the current chunk
        chunk_df = df_modified[df_modified['id'].isin(chunk)]
        
        # Extract features for the current chunk using the custom fc_parameters
        extracted_features_chunk = extract_features(
            chunk_df,
            column_id='id',
            column_sort='time',
            default_fc_parameters=fc_parameters,
            n_jobs=4,
        )
        
        # Impute missing values in the extracted features
        impute(extracted_features_chunk)
        
        # Append the extracted features to the results list
        results.append(extracted_features_chunk)
        
        # Clear memory
        del chunk_df, extracted_features_chunk
        gc.collect()
    
    # Concatenate all the results into a single DataFrame
    final_result = pd.concat(results)
    
    return final_result

# Set the chunk size N (adjust based on your memory constraints)
N = 1  # Adjust as needed

# Initialize overall metrics dictionary
overall_metrics = {}

with open('result.txt', 'a') as result_file:
    # Loop over each ID to remove
    for id_to_remove in ids_to_remove_list:
        print(f"\nProcessing with ID '{id_to_remove}' removed.")
        
        # 0. Preprocessing: Remove specific amblyope ID
        # Remove selected amblyope ID
        df_modified = time_series_df[time_series_df['id'] != id_to_remove].copy()
        
        # Extract unique IDs from the modified DataFrame
        unique_ids = df_modified['id'].unique()
        
        # Select only the required columns
        df_modified = df_modified[['id', 'time', 'O1', 'Oz', 'O2']]
        
        # Reset indexes
        df_modified.reset_index(drop=True, inplace=True)
        
        # Extract features for the current dataset
        print("Extracting features...")
        extracted_features = process_in_chunks(df_modified, N, custom_fc_parameters)
        
        # Clean the extracted features
        extracted_features_clean = extracted_features.replace([np.inf, -np.inf], np.nan).dropna(axis=1)
        
        # Ensure that the labels are aligned with the extracted features
        def get_label_from_id(id_):
            if id_.startswith('A'):
                return 1  # Amblyope
            elif id_.startswith('C'):
                return 0  # Control
            else:
                return np.nan
        
        labels = pd.DataFrame(extracted_features_clean.index, columns=['id'])
        labels['label'] = labels['id'].apply(get_label_from_id)
        labels.set_index('id', inplace=True)
        labels_aligned = labels.loc[extracted_features_clean.index]
        
        # Remove any entries with NaN labels
        valid_indices = labels_aligned['label'].notna()
        extracted_features_clean = extracted_features_clean[valid_indices]
        labels_aligned = labels_aligned[valid_indices]
        
        # 3. Define classifiers (using default parameters for simplicity)
        classifiers = {
            'Random Forest': RandomForestClassifier(random_state=42),
            'Gradient Boosting': GradientBoostingClassifier(random_state=42),
            'Neural Network': MLPClassifier(random_state=42, max_iter=1000),
            'Logistic Regression': LogisticRegression(random_state=42, max_iter=5000),
            'Support Vector Machine': SVC(random_state=42),
            'XGBoost': XGBClassifier(random_state=42, use_label_encoder=False, eval_metric='logloss')
        }
        
        # 4. Define the number of permutations
        num_permutations = 150  # As per your request
        
        # Initialize metrics dictionary for this ID
        metrics = {name: {'accuracy': [], 'precision': [], 'recall': [], 'f1_score': [], 'mcc': []} for name in classifiers.keys()}
        
        # 5. Loop over permutations
        for perm in range(num_permutations):
            print(f"\nPermutation {perm+1}/{num_permutations} for ID '{id_to_remove}' removed.")
            
            # Shuffle the labels
            np.random.seed(perm)  # For reproducibility
            shuffled_labels = labels_aligned['label'].sample(frac=1, random_state=perm).reset_index(drop=True)
            
            # Split the data into training and testing sets
            X_train, X_test, y_train, y_test = train_test_split(
                extracted_features_clean,
                shuffled_labels,
                test_size=0.25,
                random_state=42,
                stratify=shuffled_labels
            )
            
            # Loop through each classifier and evaluate
            for name, classifier in classifiers.items():
                # Suppress convergence warnings
                warnings.filterwarnings(action='ignore', category=ConvergenceWarning)
                
                print(f"Evaluating {name} for permutation {perm+1}...")
                # Create a pipeline with feature selection and the classifier
                if name in ['Neural Network', 'Logistic Regression', 'Support Vector Machine']:
                    pipeline = Pipeline([
                        ('scaler', StandardScaler()),
                        ('selector', SelectKBest(f_classif, k=50)),
                        ('classifier', classifier)
                    ])
                else:
                    pipeline = Pipeline([
                        ('selector', SelectKBest(f_classif, k=50)),
                        ('classifier', classifier)
                    ])
                
                # Fit the pipeline
                pipeline.fit(X_train, y_train)
                
                # Make predictions
                y_pred = pipeline.predict(X_test)
                
                # Calculate metrics
                accuracy = accuracy_score(y_test, y_pred)
                precision = precision_score(y_test, y_pred, zero_division=0)
                recall = recall_score(y_test, y_pred, zero_division=0)
                f1 = f1_score(y_test, y_pred, zero_division=0)
                mcc = matthews_corrcoef(y_test, y_pred)
                
                # Append metrics
                metrics[name]['accuracy'].append(accuracy)
                metrics[name]['precision'].append(precision)
                metrics[name]['recall'].append(recall)
                metrics[name]['f1_score'].append(f1)
                metrics[name]['mcc'].append(mcc)
        
        # 6. After permutations, compute mean and 95% confidence intervals
        def compute_confidence_interval(data):
            n = len(data)
            mean = np.mean(data)
            sem = stats.sem(data)
            h = sem * stats.t.ppf((1 + 0.95) / 2., n-1)
            return mean, mean - h, mean + h
        
        # Function to compute percentiles
        def compute_percentiles(data, lower_percentile=2.5, upper_percentile=97.5):
            mean = np.mean(data)
            lower = np.percentile(data, lower_percentile)
            upper = np.percentile(data, upper_percentile)
            return mean, lower, upper
        
        # Store results for this ID
        overall_metrics[id_to_remove] = {}
        
        # Print the results
        for name in classifiers.keys():
            print(f"\nResults for {name} with ID '{id_to_remove}' removed:")
            result_file.write(f"\nResults for {name} with ID '{id_to_remove}' removed:")
            overall_metrics[id_to_remove][name] = {}
            for metric_name in ['accuracy', 'precision', 'recall', 'f1_score']:
                data = metrics[name][metric_name]
                mean, lower, upper = compute_confidence_interval(data)
                overall_metrics[id_to_remove][name][metric_name] = {'mean': mean, 'ci_lower': lower, 'ci_upper': upper}
                print(f"{metric_name.capitalize()}: {mean:.4f}, 95% CI: [{lower:.4f}, {upper:.4f}]")
                result_file.write(f"{metric_name.capitalize()}: {mean:.4f}, 95% CI: [{lower:.4f}, {upper:.4f}]\n")
                
            # For MCC, compute percentiles
            mcc_data = metrics[name]['mcc']
            mcc_mean, mcc_lower, mcc_upper = compute_percentiles(mcc_data)
            overall_metrics[id_to_remove][name]['mcc'] = {'mean': mcc_mean, 'perc_lower': mcc_lower, 'perc_upper': mcc_upper}
            print(f"MCC: {mcc_mean:.4f}, Percentiles [2.5%, 97.5%]: [{mcc_lower:.4f}, {mcc_upper:.4f}]")
            result_file.write(f"MCC: {mcc_mean:.4f}, Percentiles [2.5%, 97.5%]: [{mcc_lower:.4f}, {mcc_upper:.4f}]\n")


Processing with ID 'A1' removed.
Extracting features...


Feature Extraction: 100%|██████████| 3/3 [00:04<00:00,  1.55s/it]



Permutation 1/150 for ID 'A1' removed.
Evaluating Random Forest for permutation 1...
Evaluating Gradient Boosting for permutation 1...


c:\Users\WERPELGA\AppData\Local\Programs\Python\Python39\lib\site-packages\sklearn\feature_selection\_univariate_selection.py:112: UserWarning: Features [   1  413  421  429  841  849  857 1269 1277] are constant.
  warnings.warn("Features %s are constant." % constant_features_idx, UserWarning)
c:\Users\WERPELGA\AppData\Local\Programs\Python\Python39\lib\site-packages\sklearn\feature_selection\_univariate_selection.py:113: RuntimeWarning: invalid value encountered in divide
  f = msb / msw
c:\Users\WERPELGA\AppData\Local\Programs\Python\Python39\lib\site-packages\sklearn\feature_selection\_univariate_selection.py:112: UserWarning: Features [   1  413  421  429  841  849  857 1269 1277] are constant.
  warnings.warn("Features %s are constant." % constant_features_idx, UserWarning)
c:\Users\WERPELGA\AppData\Local\Programs\Python\Python39\lib\site-packages\sklearn\feature_selection\_univariate_selection.py:113: RuntimeWarning: invalid value encountered in divide
  f = msb / msw


Evaluating Neural Network for permutation 1...
Evaluating Logistic Regression for permutation 1...
Evaluating Support Vector Machine for permutation 1...
Evaluating XGBoost for permutation 1...

Permutation 2/150 for ID 'A1' removed.
Evaluating Random Forest for permutation 2...


...

Evaluating Neural Network for permutation 150...


c:\Users\WERPELGA\AppData\Local\Programs\Python\Python39\lib\site-packages\sklearn\feature_selection\_univariate_selection.py:112: UserWarning: Features [   1  413  421  429  841  849  857 1269 1277] are constant.
  warnings.warn("Features %s are constant." % constant_features_idx, UserWarning)
c:\Users\WERPELGA\AppData\Local\Programs\Python\Python39\lib\site-packages\sklearn\feature_selection\_univariate_selection.py:113: RuntimeWarning: invalid value encountered in divide
  f = msb / msw


Evaluating Logistic Regression for permutation 150...
Evaluating Support Vector Machine for permutation 150...
Evaluating XGBoost for permutation 150...


c:\Users\WERPELGA\AppData\Local\Programs\Python\Python39\lib\site-packages\sklearn\feature_selection\_univariate_selection.py:112: UserWarning: Features [   1  413  421  429  841  849  857 1269 1277] are constant.
  warnings.warn("Features %s are constant." % constant_features_idx, UserWarning)
c:\Users\WERPELGA\AppData\Local\Programs\Python\Python39\lib\site-packages\sklearn\feature_selection\_univariate_selection.py:113: RuntimeWarning: invalid value encountered in divide
  f = msb / msw
c:\Users\WERPELGA\AppData\Local\Programs\Python\Python39\lib\site-packages\sklearn\feature_selection\_univariate_selection.py:112: UserWarning: Features [   1  413  421  429  841  849  857 1269 1277] are constant.
  warnings.warn("Features %s are constant." % constant_features_idx, UserWarning)
c:\Users\WERPELGA\AppData\Local\Programs\Python\Python39\lib\site-packages\sklearn\feature_selection\_univariate_selection.py:113: RuntimeWarning: invalid value encountered in divide
  f = msb / msw
c:\Users\W


Results for Random Forest with ID 'A9' removed:
Accuracy: 0.5231, 95% CI: [0.5014, 0.5447]
Precision: 0.5539, 95% CI: [0.5324, 0.5754]
Recall: 0.5962, 95% CI: [0.5651, 0.6273]
F1_score: 0.5642, 95% CI: [0.5407, 0.5878]
MCC: 0.0338, Percentiles [2.5%, 97.5%]: [-0.5152, 0.5476]

Results for Gradient Boosting with ID 'A9' removed:
Accuracy: 0.5077, 95% CI: [0.4861, 0.5293]
Precision: 0.5597, 95% CI: [0.5340, 0.5854]
Recall: 0.5295, 95% CI: [0.4980, 0.5611]
F1_score: 0.5257, 95% CI: [0.5024, 0.5490]
MCC: 0.0158, Percentiles [2.5%, 97.5%]: [-0.5476, 0.5476]

Results for Neural Network with ID 'A9' removed:
Accuracy: 0.5000, 95% CI: [0.4784, 0.5216]
Precision: 0.5403, 95% CI: [0.5189, 0.5617]
Recall: 0.5448, 95% CI: [0.5160, 0.5736]
F1_score: 0.5321, 95% CI: [0.5099, 0.5543]
MCC: -0.0085, Percentiles [2.5%, 97.5%]: [-0.5476, 0.5476]

Results for Logistic Regression with ID 'A9' removed:
Accuracy: 0.5169, 95% CI: [0.4946, 0.5393]
Precision: 0.5562, 95% CI: [0.5333, 0.5790]
Recall: 0.5714, 95

In [26]:
import pandas as pd
import re

# Read the file and collect blocks
blocks = []
current_block = []
with open('result.txt', 'r') as f:
    for line in f:
        line = line.strip()
        if line.startswith('Results for'):
            if current_block:
                blocks.append(current_block)
            current_block = [line]
        elif line:
            current_block.append(line)
    if current_block:
        blocks.append(current_block)

# Initialize data list
data = []

pattern_line0 = r"Results for ([^']+) with ID '([^']+)' removed:Accuracy: ([\d\.]+), 95% CI: \[([\d\.]+), ([\d\.]+)\]"
pattern_metric = r"(\w+): ([\d\.]+), 95% CI: \[([\d\.]+), ([\d\.]+)\]"
pattern_mcc = r"MCC: ([\d\.\-]+), Percentiles \[2\.5%, 97\.5%\]: \[([\d\.\-]+), ([\d\.\-]+)\]"

for block in blocks:
    record = {}
    # Line 0
    line0 = block[0]
    match = re.match(pattern_line0, line0)
    if match:
        model, ID, accuracy, acc_lower, acc_upper = match.groups()
        record['Model'] = model.strip()
        record['ID'] = ID.strip()
        record['Accuracy'] = float(accuracy)
        record['Accuracy_CI_lower'] = float(acc_lower)
        record['Accuracy_CI_upper'] = float(acc_upper)
    else:
        print(f"Line does not match pattern: {line0}")
        continue  # Skip this block if line0 does not match

    # Lines 1 to len(block)-1
    for line in block[1:]:
        if line.startswith('MCC'):
            # MCC line
            match = re.match(pattern_mcc, line)
            if match:
                mcc_value, mcc_lower, mcc_upper = match.groups()
                record['MCC'] = float(mcc_value)
                record['MCC_CI_lower'] = float(mcc_lower)
                record['MCC_CI_upper'] = float(mcc_upper)
            else:
                print(f"MCC line does not match pattern: {line}")
                continue  # Skip this block if MCC line does not match
        else:
            # Other metric lines
            match = re.match(pattern_metric, line)
            if match:
                metric_name, value, lower, upper = match.groups()
                record[metric_name] = float(value)
                record[f'{metric_name}_CI_lower'] = float(lower)
                record[f'{metric_name}_CI_upper'] = float(upper)
            else:
                print(f"Metric line does not match pattern: {line}")
                continue  # Skip this block if line does not match

    data.append(record)

# Create DataFrame
df = pd.DataFrame(data)

# Compute mean over all 'A' values per Model
metric_columns = ['Accuracy', 'Precision', 'Recall', 'F1_score', 'MCC']
ci_columns = ['Accuracy_CI_lower', 'Accuracy_CI_upper',
              'Precision_CI_lower', 'Precision_CI_upper',
              'Recall_CI_lower', 'Recall_CI_upper',
              'F1_score_CI_lower', 'F1_score_CI_upper',
              'MCC_CI_lower', 'MCC_CI_upper']

# Filter only IDs that start with 'A'
df = df[df['ID'].str.startswith('A')]

# Group by Model and compute the mean
grouped = df.groupby('Model')[metric_columns + ci_columns].mean().reset_index()

# Rename grouped DataFrame to df as per your request
df = grouped

# Output the DataFrame
print(df)


                    Model  Accuracy  Precision    Recall  F1_score       MCC  \
0       Gradient Boosting  0.508929   0.560757  0.529943  0.527114  0.018257   
1     Logistic Regression  0.516900   0.556200  0.571400  0.550600  0.030100   
2          Neural Network  0.502943   0.547086  0.541386  0.531186  0.000371   
3           Random Forest  0.521314   0.554614  0.601771  0.565571  0.029243   
4  Support Vector Machine  0.528200   0.555300  0.617100  0.574700  0.043500   
5                 XGBoost  0.510114   0.548186  0.565971  0.545200  0.012071   

   Accuracy_CI_lower  Accuracy_CI_upper  Precision_CI_lower  \
0           0.487071           0.530800            0.534686   
1           0.494600           0.539300            0.533300   
2           0.482000           0.523900            0.524486   
3           0.498686           0.543929            0.532143   
4           0.508600           0.547900            0.537200   
5           0.487129           0.533129            0.524643  

In [31]:
import pandas as pd
import re

# Read the file and collect blocks
blocks = []
current_block = []
with open('result.txt', 'r') as f:
    for line in f:
        line = line.strip()
        if line.startswith('Results for'):
            if current_block:
                blocks.append(current_block)
            current_block = [line]
        elif line:
            current_block.append(line)
    if current_block:
        blocks.append(current_block)

# Initialize data list
data = []

pattern_line0 = r"Results for ([^']+) with ID '([^']+)' removed:Accuracy: ([\d\.]+), 95% CI: \[([\d\.]+), ([\d\.]+)\]"
pattern_metric = r"(\w+): ([\d\.\-]+), 95% CI: \[([\d\.\-]+), ([\d\.\-]+)\]"
pattern_mcc = r"MCC: ([\d\.\-]+), Percentiles \[2\.5%, 97\.5%\]: \[([\d\.\-]+), ([\d\.\-]+)\]"

for block in blocks:
    record = {}
    # Line 0
    line0 = block[0]
    match = re.match(pattern_line0, line0)
    if match:
        model, ID, accuracy, acc_lower, acc_upper = match.groups()
        record['Model'] = model.strip()
        record['ID'] = ID.strip()
        record['Accuracy'] = float(accuracy)
        record['Accuracy_CI_lower'] = float(acc_lower)
        record['Accuracy_CI_upper'] = float(acc_upper)
    else:
        print(f"Line does not match pattern: {line0}")
        continue  # Skip this block if line0 does not match

    # Lines 1 to len(block)-1
    for line in block[1:]:
        if line.startswith('MCC'):
            # MCC line
            match = re.match(pattern_mcc, line)
            if match:
                mcc_value, mcc_lower, mcc_upper = match.groups()
                record['MCC'] = float(mcc_value)
                record['MCC_CI_lower'] = float(mcc_lower)
                record['MCC_CI_upper'] = float(mcc_upper)
            else:
                print(f"MCC line does not match pattern: {line}")
                continue  # Skip this block if MCC line does not match
        else:
            # Other metric lines
            match = re.match(pattern_metric, line)
            if match:
                metric_name, value, lower, upper = match.groups()
                record[metric_name] = float(value)
                record[f'{metric_name}_CI_lower'] = float(lower)
                record[f'{metric_name}_CI_upper'] = float(upper)
            else:
                print(f"Metric line does not match pattern: {line}")
                continue  # Skip this block if line does not match

    data.append(record)

# Create DataFrame
df = pd.DataFrame(data)

# Filter only IDs that start with 'A'
df = df[df['ID'].str.startswith('A')]

# Compute mean over all 'A' values per Model
metric_columns = ['Accuracy', 'Precision', 'Recall', 'F1_score', 'MCC']
ci_columns = ['Accuracy_CI_lower', 'Accuracy_CI_upper',
              'Precision_CI_lower', 'Precision_CI_upper',
              'Recall_CI_lower', 'Recall_CI_upper',
              'F1_score_CI_lower', 'F1_score_CI_upper',
              'MCC_CI_lower', 'MCC_CI_upper']

grouped = df.groupby('Model')[metric_columns + ci_columns].mean().reset_index()

# Now, create combined columns with value and CI
combined_df = pd.DataFrame()
combined_df['Model'] = grouped['Model']

for metric in metric_columns:
    mean_value = grouped[metric]
    ci_lower = grouped[f'{metric}_CI_lower']
    ci_upper = grouped[f'{metric}_CI_upper']
     # Round values to 2 decimals
    mean_value = mean_value.round(2)
    ci_lower = ci_lower.round(2)
    ci_upper = ci_upper.round(2)
    # Create combined string
    combined_metric = mean_value.round(4).astype(str) + ' [' + ci_lower.round(4).astype(str) + ', ' + ci_upper.round(4).astype(str) + ']'
    # Column name with CI
    combined_metric_name = f'{metric} CI [2.5%, 97.5%]'
    combined_df[combined_metric_name] = combined_metric

# Output the DataFrame
print(combined_df)


                    Model Accuracy CI [2.5%, 97.5%]  \
0       Gradient Boosting         0.51 [0.49, 0.53]   
1     Logistic Regression         0.52 [0.49, 0.54]   
2          Neural Network          0.5 [0.48, 0.52]   
3           Random Forest          0.52 [0.5, 0.54]   
4  Support Vector Machine         0.53 [0.51, 0.55]   
5                 XGBoost         0.51 [0.49, 0.53]   

  Precision CI [2.5%, 97.5%] Recall CI [2.5%, 97.5%]  \
0          0.56 [0.53, 0.59]        0.53 [0.5, 0.56]   
1          0.56 [0.53, 0.58]        0.57 [0.54, 0.6]   
2          0.55 [0.52, 0.57]       0.54 [0.51, 0.57]   
3          0.55 [0.53, 0.58]        0.6 [0.57, 0.63]   
4          0.56 [0.54, 0.57]       0.62 [0.59, 0.65]   
5          0.55 [0.52, 0.57]        0.57 [0.53, 0.6]   

  F1_score CI [2.5%, 97.5%] MCC CI [2.5%, 97.5%]  
0          0.53 [0.5, 0.55]   0.02 [-0.55, 0.55]  
1         0.55 [0.53, 0.57]   0.03 [-0.55, 0.54]  
2         0.53 [0.51, 0.55]     0.0 [-0.53, 0.5]  
3         0.57 [0

In [32]:
combined_df

Model Accuracy CI [2.5%, 97.5%]  \
0       Gradient Boosting         0.51 [0.49, 0.53]   
1     Logistic Regression         0.52 [0.49, 0.54]   
2          Neural Network          0.5 [0.48, 0.52]   
3           Random Forest          0.52 [0.5, 0.54]   
4  Support Vector Machine         0.53 [0.51, 0.55]   
5                 XGBoost         0.51 [0.49, 0.53]   

  Precision CI [2.5%, 97.5%] Recall CI [2.5%, 97.5%]  \
0          0.56 [0.53, 0.59]        0.53 [0.5, 0.56]   
1          0.56 [0.53, 0.58]        0.57 [0.54, 0.6]   
2          0.55 [0.52, 0.57]       0.54 [0.51, 0.57]   
3          0.55 [0.53, 0.58]        0.6 [0.57, 0.63]   
4          0.56 [0.54, 0.57]       0.62 [0.59, 0.65]   
5          0.55 [0.52, 0.57]        0.57 [0.53, 0.6]   

  F1_score CI [2.5%, 97.5%] MCC CI [2.5%, 97.5%]  
0          0.53 [0.5, 0.55]   0.02 [-0.55, 0.55]  
1         0.55 [0.53, 0.57]   0.03 [-0.55, 0.54]  
2         0.53 [0.51, 0.55]     0.0 [-0.53, 0.5]  
3         0.57 [0.54, 0.59]   0.03 [-0.53, 0.56]  
4          0.57 [0.55, 0.6]   0.04 [-0.52, 0.54]  
5         0.55 [0.52, 0.57]   0.01 [-0.56, 0.56]